# Pipeline procesamieto de datos

Definición de los Pipelines para el procesamiento de Texto de las descripciones de denuncias

## 1) Instalación de paquetes e Importacion de librerias

In [ ]:
!pip install nltk
!pip install contexto

Requirement already satisfied: nltk in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (3.6.2)
Requirement already satisfied: tqdm in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from nltk) (4.42.1)
Requirement already satisfied: regex in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from nltk) (2021.8.3)
Requirement already satisfied: joblib in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from nltk) (0.14.1)
Requirement already satisfied: click in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from nltk) (7.1.2)
Requirement already satisfied: contexto in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (0.2.0)
Requirement already satisfied: networkx==2.5.1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (2.5.1)
Requirement already satisfied: reportlab==3.5.68 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (3.5.68)
Requirement already satisfied: matplotlib>=3.3.4 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (3.4.2)
Requirement already satisfied: opencv-python>=4.5.2.54 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (4.5.3.56)
Requirement already satisfied: langid==1.1.6 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (1.1.6)
Requirement already satisfied: nltk==3.6.2 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (3.6.2)
Requirement already satisfied: pytesseract==0.3.7; python_version < "3.8.4" in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (0.3.7)
Requirement already satisfied: slate3k==0.5.3 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (0.5.3)
Requirement already satisfied: click<7.2.0,>=7.1.1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (7.1.2)
Requirement already satisfied: PyPDF2==1.26.0 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (1.26.0)
Requirement already satisfied: pdf2image==1.16.0 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (1.16.0)
Requirement already satisfied: docx2txt==0.8 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (0.8)
Requirement already satisfied: stanza>=1.2.1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (1.2.3)
Requirement already satisfied: scikit-learn>=0.24.2 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (0.24.2)
Requirement already satisfied: gensim==4.0.1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (4.0.1)
Requirement already satisfied: googletrans==2.4.0 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (2.4.0)
Requirement already satisfied: pyspellchecker==0.6.2 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (0.6.2)
Requirement already satisfied: pandas>=0.25.3 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (1.0.1)
Requirement already satisfied: spacy>=3.0.6 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (3.1.1)
Requirement already satisfied: wordcloud>=1.8.1 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (1.8.1)
Requirement already satisfied: python-docx>=0.8.11 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (0.8.11)
Requirement already satisfied: jellyfish==0.8.2 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from contexto) (0.8.2)
Requirement already satisfied: decorator<5,>=4.3 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from net

In [ ]:
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

import contexto
from contexto.limpieza import *

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data] Unzipping corpora/stopwords.zip.

In [ ]:
import sparknlp

from pyspark.ml import Pipeline, feature

from pyspark.ml.feature import OneHotEncoder, VectorAssembler, StringIndexer

from sparknlp.annotator import *
from sparknlp.common import *
from sparknlp.base import *

from sparknlp.training import *

from pyspark.sql.functions import explode
from pyspark.sql.functions import col,isnan,when,count
import pyspark.sql.functions as F

import mlflow
import mlflow.spark

print("Spark NLP version: ", sparknlp.version())
print("Apache Spark version: ", spark.version)

Spark NLP version: 3.1.1
Apache Spark version: 3.0.1

## 2) Conformación Stopwords para limpieza de texto

In [ ]:
# Generando Lista de Stop Words con NLTK
spa_stopwords = stopwords.words('spanish')
print(len(spa_stopwords))

# Generando Lista de Stop Words con Contexto DNP
contexto_stopwords = lista_stopwords()
print(len(contexto_stopwords))
nombres_todos = lista_nombres()
print(len(nombres_todos))
apellidos = lista_apellidos()
print(len(apellidos))
todos_geo = lista_geo_colombia()
print(len(todos_geo))

# Ampliando lista de stopwords
spa_stopwords.extend(contexto_stopwords)
spa_stopwords.extend(nombres_todos[0])
spa_stopwords.extend(apellidos[0])
spa_stopwords.extend(todos_geo[0])

print(len(spa_stopwords))

spa_stopwords = list(set(spa_stopwords))

print(len(spa_stopwords))


313
350
2
2
2
17401
17016

## 3) Creación de stages para el Pipeline
Trasformación de texto se definen las etapas iniciales de limpieza y luego los modelos de vectorización de texto

In [ ]:
documentAssembler = DocumentAssembler() \
      .setInputCol("DescripcionPeticion") \
      .setOutputCol("document")

sentence = SentenceDetector() \
      .setInputCols(["document"]) \
      .setOutputCol("sentence")

tokenizer = Tokenizer() \
      .setInputCols(['sentence']) \
      .setOutputCol('token')

# Pasar a minusculas todo el texto
normalizer = Normalizer() \
      .setInputCols(['token']) \
      .setOutputCol('normalized').setLowercase(True)

# note that lemmatizer needs a dictionary to pre-trained model
lemmatizer = LemmatizerModel.pretrained("lemma", "es") \
      .setInputCols(['normalized']) \
      .setOutputCol('lemma')

stopwords_cleaner = StopWordsCleaner.pretrained("stopwords_es", "es") \
      .setInputCols(['lemma']) \
      .setOutputCol('clean_lemma').setCaseSensitive(False).setStopWords(spa_stopwords)


lemma download started this may take some time.
Approximate size to download 5.1 MB
[ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][OK!]
stopwords_es download started this may take some time.
Approximate size to download 2.2 KB
[ | ][OK!]

#### 3.1) Modelo TF-IDF de vectorización de texto

In [ ]:

# finisher converts tokens to human-readable output
finisher = Finisher().setInputCols(['clean_lemma']) \
    .setOutputCols(['clean_lemma'])\
    .setOutputAsArray(True)

hashingtf = feature.HashingTF()\
    .setInputCol('clean_lemma')\
    .setOutputCol('tf')\
    .setNumFeatures(300)

idf = feature.IDF()\
    .setInputCol('tf')\
    .setOutputCol('tfidf')

#### 3.2) Modelo WordEmbeddings glove_100d

In [ ]:
glove_embeddings = WordEmbeddingsModel.pretrained('glove_100d') \
    .setInputCols(["document", "token"]) \
    .setOutputCol("embeddings")

embeddingsSentence = SentenceEmbeddings() \
      .setInputCols(["document", "embeddings"]) \
      .setOutputCol("sentence_embeddings") \
      .setPoolingStrategy("AVERAGE")

embeddingsFinisher = EmbeddingsFinisher() \
    .setInputCols(["sentence_embeddings"]) \
    .setOutputCols("finished_sentence_embeddings") \
    .setOutputAsVector(True) \
    .setCleanAnnotations(False)

explodeVectors = feature.SQLTransformer(statement="SELECT EXPLODE(finished_sentence_embeddings) AS finished_embeddings_vector, * FROM __THIS__")

glove_100d download started this may take some time.
Approximate size to download 145.3 MB
[ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][OK!]

#### 3.3) Encoding Variable Objetivo

In [ ]:
# Variable Objetivo
label_indexer = feature.StringIndexer() \
    .setInputCol('VAR_OBJETIVO') \
    .setOutputCol('label') \
    .setHandleInvalid("skip")

label_encoding = feature.OneHotEncoder() \
    .setInputCol('label') \
    .setOutputCol('label_encode')

#### 3.4) Seleccion Features Númericas y Categoricas

In [ ]:
cols=['AnoRegistroPeticion', 'MesRegistroPeticion', 'MotivoPeticion', 'RegionalCreacion', 'CanalRecepcion', 'TipoDocumentoPeticionario', 'EdadPeticionario', 'SexoPeticionario', 'GrupoEtnicoPeticionario', 'PuebloIndigenaPeticionario', 'PresentaDiscapacidadPeticionario', 'CondicionDesplazamientoPeticionario', 'HaSidoVictimaPeticionario', 'TipoDocumentoAfectado', 'EdadAfectado_Anios', 'SexoAfectado', 'GrupoEtnicoAfectado', 'PuebloIndigenaAfectado', 'PresentaDiscapacidadAfectado', 'CondicionDesplazamientoAfectado', 'horaRegistroPeticion', 'minutoRegistroPeticion', "DescripcionPeticion", 'VAR_OBJETIVO']

categoricalColumns = ["MesRegistroPeticion", "MotivoPeticion", "RegionalCreacion", "CanalRecepcion", "TipoDocumentoPeticionario", "EdadPeticionario", "SexoPeticionario", "GrupoEtnicoPeticionario", "PuebloIndigenaPeticionario", "PresentaDiscapacidadPeticionario", "CondicionDesplazamientoPeticionario", "HaSidoVictimaPeticionario", "TipoDocumentoAfectado", "SexoAfectado", "GrupoEtnicoAfectado", "PuebloIndigenaAfectado", "PresentaDiscapacidadAfectado", "CondicionDesplazamientoAfectado"]

numericalColumns = [x for x in cols if x not in categoricalColumns and x != "VAR_OBJETIVO" and x != "DescripcionPeticion"]

numericalColumns

Out[16]: ['AnoRegistroPeticion',
 'EdadAfectado_Anios',
 'horaRegistroPeticion',
 'minutoRegistroPeticion']

In [ ]:
stages1 = [documentAssembler,
           sentence,
           tokenizer,
           normalizer,
           lemmatizer,
           stopwords_cleaner,
           finisher,
           hashingtf,
           idf,
           label_indexer,
           label_encoding]
 
stages2 = [documentAssembler,
           sentence,
           tokenizer,
           glove_embeddings,
           embeddingsSentence,
           embeddingsFinisher,
           explodeVectors]

#### 3.5) StringIndexer and OneHotEncoding de Variables Categoricas

In [ ]:
categoricalColumnsclassVec = [c + "classVec" for c in categoricalColumns]


for categoricalColumn in categoricalColumns:
  print(categoricalColumn)
  ## Category Indexing with StringIndexer
  stringIndexer = StringIndexer(inputCol=categoricalColumn, outputCol = categoricalColumn+"Index").setHandleInvalid("skip")
  ## Use OneHotEncoder to convert categorical variables into binary SparseVectors
  encoder = OneHotEncoder(inputCol=categoricalColumn+"Index", outputCol=categoricalColumn+"classVec")
  ## Add stages
  stages1 += [stringIndexer, encoder]
  stages2 += [stringIndexer, encoder]


MesRegistroPeticion
MotivoPeticion
RegionalCreacion
CanalRecepcion
TipoDocumentoPeticionario
EdadPeticionario
SexoPeticionario
GrupoEtnicoPeticionario
PuebloIndigenaPeticionario
PresentaDiscapacidadPeticionario
CondicionDesplazamientoPeticionario
HaSidoVictimaPeticionario
TipoDocumentoAfectado
SexoAfectado
GrupoEtnicoAfectado
PuebloIndigenaAfectado
PresentaDiscapacidadAfectado
CondicionDesplazamientoAfectado

In [ ]:
# One Hot Encoding
#categorical_columns = ['EsPeticionHija','TipoPeticionario', 'TipoPeticion', 'MotivoPeticion', 'RegionalCreacion']

# The index of string vlaues multiple columns
#indexers = [feature.StringIndexer(inputCol=c, outputCol="{0}_indexed".format(c)).setHandleInvalid("skip") for c in categorical_columns]

# The encode of indexed vlaues multiple columns
#encoders = [feature.OneHotEncoder(dropLast=False,inputCol=indexer.getOutputCol(), outputCol="{0}_encoded".format(indexer.getOutputCol())).setHandleInvalid("skip") for indexer in indexers]

In [ ]:
assemblerInputs = categoricalColumnsclassVec + numericalColumns
assembler = VectorAssembler(inputCols = assemblerInputs,
                            outputCol = "features")

assemblerInputs = categoricalColumnsclassVec + numericalColumns + ['tfidf']
assembler1 = VectorAssembler(inputCols = assemblerInputs,
                            outputCol = "features_tfidf")

assemblerInputs = categoricalColumnsclassVec + numericalColumns + ['finished_embeddings_vector']
assembler2 = VectorAssembler(inputCols = assemblerInputs,
                            outputCol = "features_word_embeddings")


stages1 += [assembler, assembler1]

stages2 += [assembler, assembler2]

In [ ]:
stages3 = [documentAssembler,
           sentence,
           tokenizer,
           normalizer,
           lemmatizer,
           stopwords_cleaner,
           finisher,
           hashingtf,
           idf]

In [ ]:
stages4 = [documentAssembler,
           sentence,
           tokenizer,
           glove_embeddings,
           embeddingsSentence,
           embeddingsFinisher,
           explodeVectors]

##4) Importación de Datos

In [ ]:
server_name = 'jdbc:sqlserver://' + dbutils.secrets.get('blobsecret','SQLHostname')+':'+ dbutils.secrets.get('blobsecret','SQLport')
database_name = dbutils.secrets.get('blobsecret','SQLDatabase')
url = server_name + ";" + "databaseName=" + database_name + ";"
username = dbutils.secrets.get('blobsecret','SQLusername') 
password = dbutils.secrets.get('blobsecret','SQLpassword')

jdbcuser = dbutils.secrets.get('blobsecret','SQLusername')
jdbcpass = dbutils.secrets.get('blobsecret','SQLpassword')
connectionProperties = {
  "user" : jdbcuser,
  "password" : jdbcpass,
  "driver" : "com.microsoft.sqlserver.jdbc.SQLServerDriver"
}

DF_DENUNCIAS = spark.read.format("com.microsoft.sqlserver.jdbc.spark").option("url", url).option("dbtable", 'dbo.DENUNCIAS2015_2021_31032021_BASELIMPIA').option("user", username).option("password", password).load()

####Filtro de Fechas

In [ ]:
from pyspark.sql.functions import col
print((DF_DENUNCIAS.count(), len(DF_DENUNCIAS.columns)))
DF_DENUNCIAS = DF_DENUNCIAS.filter((col("AnoRegistroPeticion") != "2021"))
print((DF_DENUNCIAS.count(), len(DF_DENUNCIAS.columns)))

(1163242, 96)
(1088403, 96)

In [ ]:
DF_DENUNCIAS = DF_DENUNCIAS.filter((col("AnoRegistroPeticion") != "2020") | ~(col("MesRegistroPeticion").isin(["Jun", "Jul", "Aug", "Sep", "Oct","Nov","Dec"])))
print((DF_DENUNCIAS.count(), len(DF_DENUNCIAS.columns)))

(982084, 96)

Revisión de meses eliminados

In [ ]:
DF_DENUNCIAS.select("AnoRegistroPeticion", "MesRegistroPeticion").groupby("AnoRegistroPeticion", "MesRegistroPeticion").count().sort("AnoRegistroPeticion", ascending=False).show(truncate=False)

+-------------------+-------------------+-----+
AnoRegistroPeticion|MesRegistroPeticion|count|
+-------------------+-------------------+-----+
2020 |May |13005|
2020 |Mar |15569|
2020 |Apr |9983 |
2020 |Feb |16946|
2020 |Jan |14308|
2019 |Jul |19117|
2019 |Aug |17825|
2019 |Mar |17083|
2019 |Jun |15779|
2019 |Apr |16480|
2019 |Nov |15910|
2019 |Sep |18460|
2019 |Oct |17972|
2019 |Feb |15733|
2019 |May |19444|
2019 |Jan |14066|
2019 |Dec |13204|
2018 |Sep |20262|
2018 |Jan |14800|
2018 |Oct |20860|
+-------------------+-------------------+-----+
only showing top 20 rows

##### Revisión Variable Descripción

In [ ]:
DF_DENUNCIAS.withColumn('LenDescription', F.length('DescripcionPeticion')).select("LenDescription").orderBy(col("LenDescription").desc()).show()

+--------------+
LenDescription|
+--------------+
 32789|
 32765|
 23317|
 22782|
 21950|
 21904|
 18230|
 17952|
 17952|
 17952|
 17952|
 16840|
 16840|
 16540|
 16527|
 16325|
 16197|
 16052|
 16052|
 14953|
+--------------+
only showing top 20 rows

In [ ]:
DF_DENUNCIAS.withColumn('LenDescription', F.size(F.split(F.col('DescripcionPeticion'), ' '))).select("LenDescription").orderBy(col("LenDescription").desc()).show()

+--------------+
LenDescription|
+--------------+
 6380|
 4853|
 4166|
 3942|
 3870|
 3858|
 3847|
 3660|
 3572|
 3572|
 3383|
 3383|
 3383|
 3383|
 3280|
 3237|
 3040|
 3027|
 2935|
 2929|
+--------------+
only showing top 20 rows

####Split de la base de datos en Train y Test

In [ ]:
train, test = DF_DENUNCIAS.randomSplit(weights=[0.8, 0.2], seed=123)
print((train.count(), len(train.columns)))

(785113, 96)

##5) Training Pipelines

#### 5.1) Solo TF-IDF a la variable Descripción

In [ ]:
pipeline3 = Pipeline().setStages(stages3)
pipeline_model_3 = pipeline3.fit(train)

with mlflow.start_run():
  mlflow.spark.log_model(pipeline_model_3, "tfidf_text_featuriser")

In [ ]:
tx_train = pipeline_model_3.transform(train)
display(tx_train)

NumeroDocAfectado NumeroPeticion EsPeticionHija fechaRegistroPeticion AnoRegistroPeticion MesRegistroPeticion TipoPeticion MotivoPeticion RegionalCreacion CZCreacion RegionalDireccionada CZDireccionado CanalRecepcion TipoDocumentoPeticionario NumeroDocPeticionario NombresApellidosPeticionario PrimerNombrePeticionario SegundoNombrePeticionario PrimerApellidoPeticionario SegundoApellidoPeticionario DepartamentoPeticionario MunicipioPeticionario CodDptoPeticionario CodMunicipioPeticionario BarrioVeredaPeticionario DireccionPeticionario SenalesParticularesUbicacionPeticonarioRural DetalleTipoZonaPeticionario DetalleZonaPeticionario EdadPeticionario SexoPeticionario GrupoEtnicoPeticionario PuebloIndigenaPeticionario PresentaDiscapacidadPeticionario CualDiscapacidadPeticionario CondicionDesplazamientoPeticionario HaSidoVictimaPeticionario EstadoPeticion TipoDocumentoAfectado NombresApellidosAfectado PrimerNombreAfectado SegundoNombreAfectado PrimerApellidoAfectado SegundoApellidoAfectado DepartamentoAfectado MunicipioAfectado CodDptoAfectado CodMunicipioAfectado BarrioVeredaAfectado DireccionAfectado ObsParticUbicaAfectado DetalleTipoZonAfectado DetalleZonAfectado FechaNacAfectado SexoAfectado GrupoEtnicoAfectado PuebloIndigenaAfectado PresentaDiscapacidadAfectado CualDiscapacidadAfectado CondicionDesplazamientoAfectado PrimerMotivoIngreso UltimoMotivoIngreso DescripcionPeticion TipoPeticionario CategorizacionPRD_165 TipoDemandado D_CONSTATADAS CONSTATACION Val_Constatacion RAVD_Constatadas TIPO_PETICION PRD_160_FECHA_APERTURA ANIO MES UNFICADO_MOTIVO_INGRESO PRD_760_CIERRE_PROCESO_RESTABLECIMIENTO FECHA_ACTUACION_MAS_RECIENTE MEDIDA_ACTUACION_MAS_RECIENTE MEDIDA_TOMADA_ULTIMA PRD_165 cod_mpio cod_dpto Coord_x_auto_enc Coord_y_auto_enc Cod_vereda prob_maltrato prob_vsexual ide_edificacion Ord_vivienda id_registro llave_hogar horaRegistroPeticion minutoRegistroPeticion VAR_OBJETIVO EdadAfectado_Anios EdadAfectado_Calculada clean_lemma tf tfidf null 14221308 SI 2017-05-03 2017 May Solicitud de Restablecimiento de Derechos (SRD) Maltrato BOGOTA CZ SANTA FE BOGOTA CZ ENGATIVA Correo Electrónico ND SD - 210938456952208 CARMENZA GUTIERREZ CORRDINADORA GRUPO DE PROTECCION ICBF REGIONAL BOGOTA CARMENZA GUTIERREZ CORRDINADORA GRUPO DE PROTECCION ICBF REGIONAL BOGOTA null VALOR NULO VALOR NULO 0 0 Ninguno null null Dispersa Urbana ND F ND ND ND null ND ND Cerrada ND MARIA MERY MUÑOZ GUERRERO MARIA MERY MUÑOZ GUERRERO BOYACÁ TUNJA 15 15001 null VEREDA HUERTA CHICA AL LADO DE LA VEREDA BARON GALLERO null null Urbana 2000-07-31 F INDÍGENA ND ND ND ND null null Por medio del presente remito oficio radicado con el número E-2017-128000-0101 de la Unidad Nacional de Protección, en la cual se pone en conocimiento una presunta situación de riesgo en la que se encuentran los niños, niñas y adolescentes Jorge Eduardo Becerra Begoya, Esteban Becerra Begoya, Javier Balbuena Begoya, Luisa Fernanda Begoya y David Santiago Castiblanco Begoya.En ese sentido, conforme al factor de competencia territorial y funcional contenido en el artículo 97 de la Ley 1098 de 2006, se requiere que desde el Centro Zonal se designe un equipo de Defensoría para realizar verificación del estado de cumplimiento de derechos de los menores de edad y adelantar la acciones a que haya a lugar para el efectivo restablecimiento de sus derechos. Para los fines pertinentes se informa que los menores de edad residen en la Calle 12 D Bis No. 1  35, apartamento 301 , en la ciudad de Bogotá D.C. y pueden contactarse en el abonado celular 316-7179386.Al respecto, agradezco su colaboración creando la petición en el Sistema de Información Misional-SlM 1 y una vez esto, por favor remitir a esta Coordinación a través de la 1 El Instituto Colombiano de Bienestar Familiar, cuenta con un Sistema de Información Misional SIM- desarrollado, para cubrir las necesidades de información de este, que se originan en sus procesos misionales; dicho sistema es una herramienta que sirve de apoyo a las acciones 

#### 5.2) Solo Word Embedding a la variable Descripción

In [ ]:
pipeline4 = Pipeline().setStages(stages4)

pipeline_model_4 = pipeline4.fit(train)

with mlflow.start_run():
  mlflow.spark.log_model(pipeline_model_4, "word_embedding_text_featuriser")

In [ ]:
tx_train = pipeline_model_4.transform(train)
display(tx_train)

finished_embeddings_vector NumeroDocAfectado NumeroPeticion EsPeticionHija fechaRegistroPeticion AnoRegistroPeticion MesRegistroPeticion TipoPeticion MotivoPeticion RegionalCreacion CZCreacion RegionalDireccionada CZDireccionado CanalRecepcion TipoDocumentoPeticionario NumeroDocPeticionario NombresApellidosPeticionario PrimerNombrePeticionario SegundoNombrePeticionario PrimerApellidoPeticionario SegundoApellidoPeticionario DepartamentoPeticionario MunicipioPeticionario CodDptoPeticionario CodMunicipioPeticionario BarrioVeredaPeticionario DireccionPeticionario SenalesParticularesUbicacionPeticonarioRural DetalleTipoZonaPeticionario DetalleZonaPeticionario EdadPeticionario SexoPeticionario GrupoEtnicoPeticionario PuebloIndigenaPeticionario PresentaDiscapacidadPeticionario CualDiscapacidadPeticionario CondicionDesplazamientoPeticionario HaSidoVictimaPeticionario EstadoPeticion TipoDocumentoAfectado NombresApellidosAfectado PrimerNombreAfectado SegundoNombreAfectado PrimerApellidoAfectado SegundoApellidoAfectado DepartamentoAfectado MunicipioAfectado CodDptoAfectado CodMunicipioAfectado BarrioVeredaAfectado DireccionAfectado ObsParticUbicaAfectado DetalleTipoZonAfectado DetalleZonAfectado FechaNacAfectado SexoAfectado GrupoEtnicoAfectado PuebloIndigenaAfectado PresentaDiscapacidadAfectado CualDiscapacidadAfectado CondicionDesplazamientoAfectado PrimerMotivoIngreso UltimoMotivoIngreso DescripcionPeticion TipoPeticionario CategorizacionPRD_165 TipoDemandado D_CONSTATADAS CONSTATACION Val_Constatacion RAVD_Constatadas TIPO_PETICION PRD_160_FECHA_APERTURA ANIO MES UNFICADO_MOTIVO_INGRESO PRD_760_CIERRE_PROCESO_RESTABLECIMIENTO FECHA_ACTUACION_MAS_RECIENTE MEDIDA_ACTUACION_MAS_RECIENTE MEDIDA_TOMADA_ULTIMA PRD_165 cod_mpio cod_dpto Coord_x_auto_enc Coord_y_auto_enc Cod_vereda prob_maltrato prob_vsexual ide_edificacion Ord_vivienda id_registro llave_hogar horaRegistroPeticion minutoRegistroPeticion VAR_OBJETIVO EdadAfectado_Anios EdadAfectado_Calculada document sentence token embeddings sentence_embeddings finished_sentence_embeddings Map(vectorType -> dense, length -> 100, values -> List(0.1247943639755249, -0.37913817167282104, -9.379128459841013E-4, 0.1307835727930069, 0.11667698621749878, 0.12799760699272156, 0.4227323830127716, 0.37434959411621094, 0.47340890765190125, 0.010271463543176651, 0.1866058111190796, -0.1370270550251007, -0.20047545433044434, 0.04890558496117592, 0.1785443127155304, -0.2507151663303375, 0.16597777605056763, -0.006326872855424881, 0.026801861822605133, 0.23156125843524933, 0.3580092191696167, 0.11770012229681015, -0.13348762691020966, 0.1842212975025177, 0.11740290373563766, -0.025210266932845116, -0.08794791251420975, -0.5365302562713623, 0.25772252678871155, -0.18948894739151, -0.12462767213582993, -0.3277173638343811, -0.10612885653972626, 0.21520531177520752, 0.12344085425138474, 0.1891361027956009, 0.3679409921169281, -0.04831067845225334, 0.16433757543563843, 0.16240622103214264, 0.24055057764053345, -0.14284245669841766, -0.2444963902235031, -0.39805448055267334, 0.3446829915046692, -0.1359759420156479, -0.3410946726799011, -0.18504494428634644, -0.623452365398407, 0.02812468633055687, -0.33855104446411133, 0.4837980568408966, -0.20937463641166687, -0.00567149231210351, -0.28337088227272034, -1.0214629173278809, 0.04295411705970764, 0.23144999146461487, 0.2731606662273407, 0.3305217921733856, -0.33981406688690186, -0.12625150382518768, -0.25531548261642456, -0.6738394498825073, 0.05818033963441849, -0.10038665682077408, 0.04522521421313286, -0.17809389531612396, 0.01996416598558426, 0.4261936545372009, 0.29791945219039917, 0.38317549228668213, -0.13458804786205292, -0.33184313774108887, 0.15474797785282135, -0.23897819221019745, 0.032623421400785446, -0.12581652402877808, -0.4051235616207123, 0.07564129680395126, 0.24824362993240356, -0.3294508457183838, -0.14363597333431244, -0.23841138184070587, -0.1992359459400177, 0.009294208139181137, -0.2652205228805542, -0.17213183641433716, 0.253255158662796

#### 5.3) Pipeline Completo One Hot Ecoding, TF-IDF y Label Encoding

In [ ]:
df = DF_DENUNCIAS.select(cols).dropna(subset=cols)
print((df.count(), len(df.columns)))
train, test = df.randomSplit(weights=[0.8, 0.2], seed=123)
print((train.count(), len(train.columns)))

(948761, 24)
(758498, 24)

In [ ]:
pipeline1 = Pipeline().setStages(stages1)
pipeline_model = pipeline1.fit(train)

with mlflow.start_run():
  mlflow.spark.log_model(pipeline_model, "text_featuriser_tfidf")

In [ ]:
tx_train = pipeline_model.transform(train)

display(tx_train)

AnoRegistroPeticion MesRegistroPeticion MotivoPeticion RegionalCreacion CanalRecepcion TipoDocumentoPeticionario EdadPeticionario SexoPeticionario GrupoEtnicoPeticionario PuebloIndigenaPeticionario PresentaDiscapacidadPeticionario CondicionDesplazamientoPeticionario HaSidoVictimaPeticionario TipoDocumentoAfectado EdadAfectado_Anios SexoAfectado GrupoEtnicoAfectado PuebloIndigenaAfectado PresentaDiscapacidadAfectado CondicionDesplazamientoAfectado horaRegistroPeticion minutoRegistroPeticion DescripcionPeticion VAR_OBJETIVO clean_lemma tf tfidf label label_encode MesRegistroPeticionIndex MesRegistroPeticionclassVec MotivoPeticionIndex MotivoPeticionclassVec RegionalCreacionIndex RegionalCreacionclassVec CanalRecepcionIndex CanalRecepcionclassVec TipoDocumentoPeticionarioIndex TipoDocumentoPeticionarioclassVec EdadPeticionarioIndex EdadPeticionarioclassVec SexoPeticionarioIndex SexoPeticionarioclassVec GrupoEtnicoPeticionarioIndex GrupoEtnicoPeticionarioclassVec PuebloIndigenaPeticionarioIndex PuebloIndigenaPeticionarioclassVec PresentaDiscapacidadPeticionarioIndex PresentaDiscapacidadPeticionarioclassVec CondicionDesplazamientoPeticionarioIndex CondicionDesplazamientoPeticionarioclassVec HaSidoVictimaPeticionarioIndex HaSidoVictimaPeticionarioclassVec TipoDocumentoAfectadoIndex TipoDocumentoAfectadoclassVec SexoAfectadoIndex SexoAfectadoclassVec GrupoEtnicoAfectadoIndex GrupoEtnicoAfectadoclassVec PuebloIndigenaAfectadoIndex PuebloIndigenaAfectadoclassVec PresentaDiscapacidadAfectadoIndex PresentaDiscapacidadAfectadoclassVec CondicionDesplazamientoAfectadoIndex CondicionDesplazamientoAfectadoclassVec features features_tfidf 2015 Apr Abandono_Amenaza AMAZONAS Escrito ND ND M ND ND ND ND ND ND 1.366 F ND ND ND ND 15 3 OFICIO RADICADO INTERNO N° 136778 DEL 6 DE ABRIL; LA MODALIDAD INSTITUCIONAL Y MODALIDAD FAMILIAR (CDI) INFORMA QUE EN UNAS DE SUS VISITAS A SUS BENEFICIARIOS EN LA COMUNIDAD DE LA PLAYA ENCONTRO QUE LOS NIÑOS SHAIRA ADAIA MESA SINARAGUA DE UN AÑOS DE EDAD Y ADAIFA ALEXANDRA SINARAGUA PINTO DE 4 AÑOS; SE ENCUENTRAN BAJO EL CUIDADO DE LA TIA MATERNA LUISA SINARAGUA PINTO DE 17 AÑOS LOS CUALES COGIO ESTE ROL POR MOTIVOS QUE SUS PROGENITORES SE ENCUENTRAN PRIVADOS DE LA LIBERTAD HACE 2 MESES. verdadera_nopard List(oficiar, radicar, internar, n, modalidad, institucional, modalidad, familiar, cdi, informar, unir, visita, beneficiario, comunidad, playa, encontro, mesar, sinaragua, año, edad, adaifa, sinaragua, pintar, año, encontrar, bajar, cuidar, tia, sinaragua, pintar, año, cogio, rol, motivo, progenitor, encontrar, privar, libertar, hacer, mes) Map(vectorType -> sparse, length -> 600, indices -> List(3, 10, 53, 57, 73, 88, 103, 123, 127, 134, 146, 180, 191, 228, 243, 244, 276, 305, 340, 362, 389, 399, 449, 463, 465, 496, 500, 508, 518, 519, 538, 555, 581), values -> List(1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0)) Map(vectorType -> sparse, length -> 600, indices -> List(3, 10, 53, 57, 73, 88, 103, 123, 127, 134, 146, 180, 191, 228, 243, 244, 276, 305, 340, 362, 389, 399, 449, 463, 465, 496, 500, 508, 518, 519, 538, 555, 581), values -> List(1.684387670156915, 1.3667365727640248, 3.530742670604047, 3.603088907473776, 8.683325780582567, 1.4479346954848866, 2.2167741807920502, 3.224581612546561, 2.817137823377579, 8.158261704173942, 1.071261024324265, 7.001101988143453, 2.4687230456098415, 1.726071053001195, 2.0910194196372713, 2.292696314088277, 0.9516562558357581, 1.424451181507772, 2.1072870062923776, 2.07148374507373, 2.091684671283357, 3.53070478248765, 1.0824123092211915, 3.7203273071447636, 0.46147538698991863, 4.800741185659175, 1.7885172104999005, 0.7693916939857925, 0.7294637791957275, 3.126579259308542, 3.410306728755478, 1.4555156581810056, 3.758985778568744)) 1.0 Map(vectorType -> sparse, length -> 4, indices -> List(1), values -> List(1.0)) 4.0 Map(vectorType -> sparse, length -> 11, indi

#### 5.4) Pipeline Completo One Hot Ecoding, Word Embedding y Label Encoding

In [ ]:
pipeline2 = Pipeline().setStages(stages2)

pipeline_model2 = pipeline2.fit(train)


with mlflow.start_run():
  mlflow.spark.log_model(pipeline_model2, "text_featuriser_wordembbeding")

##6) Prueba de Carge del Pipeline con ML FLOW

In [ ]:
# Para cargar el pipeline

import mlflow
import mlflow.spark

solo_word_embedding = "runs:/abd6d3995aaf4c65b2577b73a9be62cf/word_embedding_text_featuriser"
solo_tfidf = 'runs:/02cee8d29a894ebc86ace1eb965e0d12/tfidf_text_featuriser'

full_word_embedding = 'runs:/d3d7464f96a34255ba2df175a491b8dd/text_featuriser_wordembbeding'
full_tfidf='runs:/94e3ef997aa144989e4cf7e18fd8f702/text_featuriser_tfidf'


pipeline = mlflow.spark.load_model(solo_word_embedding)

tx_train = pipeline.transform(train)
display(tx_train)

2021/08/09 15:31:27 INFO mlflow.spark: 'runs:/abd6d3995aaf4c65b2577b73a9be62cf/word_embedding_text_featuriser' resolved as 'dbfs:/databricks/mlflow-tracking/3030803122807175/abd6d3995aaf4c65b2577b73a9be62cf/artifacts/word_embedding_text_featuriser'
2021/08/09 15:31:27 INFO mlflow.spark: File 'dbfs:/databricks/mlflow-tracking/3030803122807175/abd6d3995aaf4c65b2577b73a9be62cf/artifacts/word_embedding_text_featuriser/sparkml' not found on DFS. Will attempt to upload the file.
2021/08/09 15:32:19 INFO mlflow.spark: Copied SparkML model to /tmp/mlflow/e5fa6580-c9f3-422f-922e-a47a261cf4d2

finished_embeddings_vector NumeroDocAfectado NumeroPeticion EsPeticionHija fechaRegistroPeticion AnoRegistroPeticion MesRegistroPeticion TipoPeticion MotivoPeticion RegionalCreacion CZCreacion RegionalDireccionada CZDireccionado CanalRecepcion TipoDocumentoPeticionario NumeroDocPeticionario NombresApellidosPeticionario PrimerNombrePeticionario SegundoNombrePeticionario PrimerApellidoPeticionario SegundoApellidoPeticionario DepartamentoPeticionario MunicipioPeticionario CodDptoPeticionario CodMunicipioPeticionario BarrioVeredaPeticionario DireccionPeticionario SenalesParticularesUbicacionPeticonarioRural DetalleTipoZonaPeticionario DetalleZonaPeticionario EdadPeticionario SexoPeticionario GrupoEtnicoPeticionario PuebloIndigenaPeticionario PresentaDiscapacidadPeticionario CualDiscapacidadPeticionario CondicionDesplazamientoPeticionario HaSidoVictimaPeticionario EstadoPeticion TipoDocumentoAfectado NombresApellidosAfectado PrimerNombreAfectado SegundoNombreAfectado PrimerApellidoAfectado SegundoApellidoAfectado DepartamentoAfectado MunicipioAfectado CodDptoAfectado CodMunicipioAfectado BarrioVeredaAfectado DireccionAfectado ObsParticUbicaAfectado DetalleTipoZonAfectado DetalleZonAfectado FechaNacAfectado SexoAfectado GrupoEtnicoAfectado PuebloIndigenaAfectado PresentaDiscapacidadAfectado CualDiscapacidadAfectado CondicionDesplazamientoAfectado PrimerMotivoIngreso UltimoMotivoIngreso DescripcionPeticion TipoPeticionario CategorizacionPRD_165 TipoDemandado D_CONSTATADAS CONSTATACION Val_Constatacion RAVD_Constatadas TIPO_PETICION PRD_160_FECHA_APERTURA ANIO MES UNFICADO_MOTIVO_INGRESO PRD_760_CIERRE_PROCESO_RESTABLECIMIENTO FECHA_ACTUACION_MAS_RECIENTE MEDIDA_ACTUACION_MAS_RECIENTE MEDIDA_TOMADA_ULTIMA PRD_165 cod_mpio cod_dpto Coord_x_auto_enc Coord_y_auto_enc Cod_vereda prob_maltrato prob_vsexual ide_edificacion Ord_vivienda id_registro llave_hogar horaRegistroPeticion minutoRegistroPeticion VAR_OBJETIVO EdadAfectado_Anios EdadAfectado_Calculada document sentence token embeddings sentence_embeddings finished_sentence_embeddings Map(vectorType -> dense, length -> 100, values -> List(0.1247943639755249, -0.37913817167282104, -9.379128459841013E-4, 0.1307835727930069, 0.11667698621749878, 0.12799760699272156, 0.4227323830127716, 0.37434959411621094, 0.47340890765190125, 0.010271463543176651, 0.1866058111190796, -0.1370270550251007, -0.20047545433044434, 0.04890558496117592, 0.1785443127155304, -0.2507151663303375, 0.16597777605056763, -0.006326872855424881, 0.026801861822605133, 0.23156125843524933, 0.3580092191696167, 0.11770012229681015, -0.13348762691020966, 0.1842212975025177, 0.11740290373563766, -0.025210266932845116, -0.08794791251420975, -0.5365302562713623, 0.25772252678871155, -0.18948894739151, -0.12462767213582993, -0.3277173638343811, -0.10612885653972626, 0.21520531177520752, 0.12344085425138474, 0.1891361027956009, 0.3679409921169281, -0.04831067845225334, 0.16433757543563843, 0.16240622103214264, 0.24055057764053345, -0.14284245669841766, -0.2444963902235031, -0.39805448055267334, 0.3446829915046692, -0.1359759420156479, -0.3410946726799011, -0.18504494428634644, -0.623452365398407, 0.02812468633055687, -0.33855104446411133, 0.4837980568408966, -0.20937463641166687, -0.00567149231210351, -0.28337088227272034, -1.0214629173278809, 0.04295411705970764, 0.23144999146461487, 0.2731606662273407, 0.3305217921733856, -0.33981406688690186, -0.12625150382518768, -0.25531548261642456, -0.6738394498825073, 0.05818033963441849, -0.10038665682077408, 0.04522521421313286, -0.17809389531612396, 0.01996416598558426, 0.4261936545372009, 0.29791945219039917, 0.38317549228668213, -0.13458804786205292, -0.33184313774108887, 0.15474797785282135, -0.23897819221019745, 0.032623421400785446, -0.12581652402877808, -0.4051235616207123, 0.07564129680395126, 0.24824362993240356, -0.3294508457183838, -0.14363597333431244, -0.23841138184070587, -0.1992359459400177, 0.009294208139181137, -0.2652205228805542, -0.17213183641433716, 0.253255158662796

In [ ]:
input_text_dim = len(tx_train.select("finished_embeddings_vector").first()[0])

In [ ]:
input_text_dim

Out[10]: 100